<a href="https://colab.research.google.com/github/fernanda-valente-postgraduate/pos-graduacao-ciencia-de-dados/blob/main/projeto-sprint-3/Fernanda_Valente_MVP_Maching_Learning_Notebook_2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# MVP da Pós-graduação em Ciência de Dados e Analytics - Sprint Maching Learning & Analytics
## Aluna: Fernanda Pires Valente
**Notebook 2**

O trabalho deste MVP está dividido em 2 notebooks.

No notebook 1 fizemos as seguintes etapas:

1.   Objetivo do projeto
2.   Origem e descrição dos dados
3.   Obtenção dos dados
4.   Análise dos dados
5.   Pré-Processamento - Parte 1
6.   Divisão dos dados em Treinamento e Teste
7.   Pré-Processamento - Parte 2

No notebook 2 (este notebook) iremos dividir os dados em treinamento e teste, construir o modelo de Rede Neural (LSTM), treinar e avaliar o modelo. Por ser um continuação do primeiro notebook iremos começar do item 8.







## Bibliotecas

In [ ]:
!pip install scikeras

In [ ]:
#Imports

import os
import time
import zipfile
import warnings
import numpy as np
import pandas as pd

from google.colab import files
from transformers import pipeline
from tensorflow.keras.models import Sequential
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.optimizers import Adam, RMSprop, SGD
from tensorflow.keras.layers import LSTM, Dense, Dropout, BatchNormalization
from scikeras.wrappers import KerasClassifier
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import train_test_split, GridSearchCV




## Importando os arquivos

Primeiro vamos importar os arquivos relevantes para esse projeto.

In [ ]:
# Baixando os arquivos
!wget -O train_df.csv https://raw.githubusercontent.com/fernanda-valente-postgraduate/pos-graduacao-ciencia-de-dados/main/projeto-sprint-3/train_df.csv
!wget -O test_df.csv https://raw.githubusercontent.com/fernanda-valente-postgraduate/pos-graduacao-ciencia-de-dados/main/projeto-sprint-3/test_df.csv


!wget -O index_to_word_ste.csv https://raw.githubusercontent.com/fernanda-valente-postgraduate/pos-graduacao-ciencia-de-dados/main/projeto-sprint-3/index_to_word_ste.csv
!wget -O index_to_word_lem.csv https://raw.githubusercontent.com/fernanda-valente-postgraduate/pos-graduacao-ciencia-de-dados/main/projeto-sprint-3/index_to_word_lem.csv

!wget -O word_to_index_ste.csv https://raw.githubusercontent.com/fernanda-valente-postgraduate/pos-graduacao-ciencia-de-dados/main/projeto-sprint-3/word_to_index_ste.csv
!wget -O word_to_index_lem.csv https://raw.githubusercontent.com/fernanda-valente-postgraduate/pos-graduacao-ciencia-de-dados/main/projeto-sprint-3/word_to_index_lem.csv

--2024-12-10 13:20:59--  https://raw.githubusercontent.com/fernanda-valente-postgraduate/pos-graduacao-ciencia-de-dados/main/projeto-sprint-3/train_df.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 19917835 (19M) [text/plain]
Saving to: ‘train_df.csv’

train_df.csv        100%[===================>]  19.00M   116MB/s    in 0.2s    

2024-12-10 13:21:00 (116 MB/s) - ‘train_df.csv’ saved [19917835/19917835]

--2024-12-10 13:21:00--  https://raw.githubusercontent.com/fernanda-valente-postgraduate/pos-graduacao-ciencia-de-dados/main/projeto-sprint-3/test_df.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.10

Carregando os arquivos para o notebook

In [ ]:
train_df = pd.read_csv('train_df.csv')
test_df = pd.read_csv('test_df.csv')

index_to_word_ste = pd.read_csv('index_to_word_ste.csv', index_col=0).to_dict()['word']
index_to_word_lem = pd.read_csv('index_to_word_lem.csv', index_col=0).to_dict()['word']

word_to_index_ste = pd.read_csv('word_to_index_ste.csv', index_col=0).to_dict()
word_to_index_lem = pd.read_csv('word_to_index_lem.csv', index_col=0).to_dict()


Verificando como estão os arquivos:

In [ ]:
train_df.head(5)

rotulo                                          avaliacao  \
0  NEGATIVE  The app has started logging me out when I rest...   
1  POSITIVE  This app plays so many great songs and albums ...   
2  NEGATIVE  It's always been my preferred streaming servic...   
3  NEGATIVE  i recently got premium and everytime i skip to...   
4  POSITIVE                                      Gurthan Singh   

                               sequencias_padded_ste  \
0  [1774, 2970, 2951, 1685, 12, 1519, 1454, 1633,...   
1  [3079, 1823, 1893, 1831, 481, 2072, 3126, 2033...   
2  [426, 858, 1756, 2287, 2341, 2341, 3053, 971, ...   
3  [290, 1438, 2841, 1936, 671, 2976, 208, 0, 0, ...   
4  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                               sequencias_padded_lem  
0  [462, 3799, 3936, 2283, 2917, 2063, 549, 2204,...  
1  [4119, 324, 2542, 2468, 2176, 2783, 592, 2729,...  
2  [753, 3097, 3764, 2221, 3146, 3146, 4085, 1338...  
3  [3216, 1951, 3785, 2963, 928, 3970, 271, 0, 0,...  
4  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...

In [ ]:
test_df.head(5)

rotulo                                          avaliacao  \
0  POSITIVE  Great App, VERY easy to use the only thing I w...   
1  POSITIVE  Good, but on mobile I can only listen to my pl...   
2  POSITIVE  Can listen even if phone is not in Spotify win...   
3  NEGATIVE  New update is buggy. Now playing keeps disappe...   
4  POSITIVE  Mind-blowing very lovable app for me ðŸ‘ŒðŸ˜ð...   

                               sequencias_padded_ste  \
0  [1893, 2758, 1454, 1248, 1959, 3017, 1454, 301...   
1  [2463, 863, 340, 3154, 1484, 1369, 0, 0, 0, 0,...   
2  [421, 1685, 1613, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0...   
3  [1087, 2367, 320, 1405, 2555, 2025, 1405, 2971...   
4  [2615, 0, 1486, 204, 2428, 434, 2269, 2463, 15...   

                               sequencias_padded_lem  
0  [2542, 4047, 1972, 1701, 2634, 4034, 1972, 403...  
1  [3296, 2225, 448, 4220, 3687, 1849, 0, 0, 0, 0...  
2  [565, 2283, 2183, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0...  
3  [1485, 2829, 321, 1900, 2766, 2719, 1900, 711,...  
4  [3486, 0, 2024, 265, 498, 598, 3058, 3296, 209...

In [ ]:
result = list(index_to_word_ste.values())[:10]
print(result)

['asf', 'disgrac', 'oper', 'primium', 'layout', 'theme', 'coz', 'chrome', 'agenda', 'am']


In [ ]:
result = list(index_to_word_lem.values())[:10]
print(result)

['unfortunate', 'unexpected', 'asf', 'layout', 'primium', 'improving', 'theme', 'coz', 'chrome', 'agenda']


In [ ]:
result = list(word_to_index_lem.values())[:10]
print(result)

[{'unfortunate': 1, 'unexpected': 2, 'asf': 3, 'layout': 4, 'primium': 5, 'improving': 6, 'theme': 7, 'coz': 8, 'chrome': 9, 'agenda': 10, 'am': 11, 'depressed': 12, 'reboots': 13, 'excitement': 14, 'feed': 15, 'behaves': 16, 'fat': 17, 'slowly': 18, 'stage': 19, 'fitness': 20, 'counting': 21, 'relevant': 22, 'purposely': 23, 'streamer': 24, 'hello': 25, 'essentially': 26, 'advertisement': 27, 'grip': 28, 'reorganize': 29, 'spotifyit': 30, 'yesterday': 31, 'replaced': 32, 'increased': 33, 'lucky': 34, 'managing': 35, 'jazz': 36, 'goood': 37, 'sequence': 38, 'player': 39, 'wing': 40, 'link': 41, 'mom': 42, 'sony': 43, 'bothersome': 44, 'typically': 45, 'gained': 46, 'žðÿ': 47, 'relation': 48, 'alphabetical': 49, 'capability': 50, 'stuck': 51, 'beginning': 52, 'litsen': 53, 'handsfree': 54, 'peace': 55, 'advertisment': 56, 'denies': 57, 'gif': 58, 'filtering': 59, 'jungkook': 60, 'single': 61, 'advertisments': 62, 'term': 63, 'connected': 64, 'selected': 65, 'searched': 66, 'encounter': 

In [ ]:
result = list(word_to_index_ste.values())[:10]
print(result)

[{'asf': 1, 'disgrac': 2, 'oper': 3, 'primium': 4, 'layout': 5, 'theme': 6, 'coz': 7, 'chrome': 8, 'agenda': 9, 'am': 10, 'feed': 11, 'wherea': 12, 'imagin': 13, 'fat': 14, 'stage': 15, 'unlimit': 16, 'creepi': 17, 'kbp': 18, 'streamer': 19, 'hello': 20, 'bust': 21, 'grip': 22, 'spotifyit': 23, 'yesterday': 24, 'fantast': 25, 'piti': 26, 'verg': 27, 'jazz': 28, 'goood': 29, 'player': 30, 'wing': 31, 'link': 32, 'mom': 33, 'curiou': 34, 'žðÿ': 35, 'mainli': 36, 'stuck': 37, 'litsen': 38, 'unexpectedli': 39, 'gif': 40, 'jungkook': 41, 'term': 42, 'conspiraci': 43, 'simultan': 44, 'creator': 45, 'spotifi': 46, 'bare': 47, 'insist': 48, 'mai': 49, 'begin': 50, 'day': 51, 'spent': 52, 'intern': 53, 'today': 54, 'capabl': 55, 'discount': 56, 'descript': 57, 'potenti': 58, 'find': 59, 'discov': 60, 'sign': 61, 'pauseplayskip': 62, 'subscrib': 63, 'bengali': 64, 'absolutley': 65, 'wil': 66, 'unrespons': 67, 'concert': 68, 'ang': 69, 'launch': 70, 'aspect': 71, 'pic': 72, 'similar': 73, 'cheap'

## Relembrando pontos importantes do notebook 1

Relembrando o que vimos no notebook 1:
*   Identificamos que temos algumas linhas duplicadas, vamos gerar um conjunto de dados sem essa duplicidade e ver como a variável rótulo fica distribuída.

Revendo a distribuição da variável rótulo:

In [ ]:
# vendo como a variável target está distribuída
print("\nDistribuição de classes (valor absoluto):")
print(train_df['rotulo'].value_counts())
print("\nDistribuição de classes (representatividade):")
print(train_df['rotulo'].value_counts(normalize=True))

print("\n----------------------------------")

print("\nDistribuição de classes (valor absoluto):")
print(test_df['rotulo'].value_counts())
print("\nDistribuição de classes (representatividade):")
print(test_df['rotulo'].value_counts(normalize=True))


Distribuição de classes (valor absoluto):
rotulo
NEGATIVE    23559
POSITIVE    18589
Name: count, dtype: int64

Distribuição de classes (representatividade):
rotulo
NEGATIVE    0.558959
POSITIVE    0.441041
Name: proportion, dtype: float64

----------------------------------

Distribuição de classes (valor absoluto):
rotulo
NEGATIVE    5864
POSITIVE    4674
Name: count, dtype: int64

Distribuição de classes (representatividade):
rotulo
NEGATIVE    0.556462
POSITIVE    0.443538
Name: proportion, dtype: float64


In [ ]:
# Remover duplicatas com base em todas as colunas
train_df_sem_dup = train_df.drop_duplicates()
test_df_sem_dup = test_df.drop_duplicates()

Vendo a distribuição da variável rótulo depois de retirar linhas duplicadas:

In [ ]:
# vendo como a variável target está distribuída do df sem duplicidade
print("\nDistribuição de classes (valor absoluto):")
print(train_df_sem_dup['rotulo'].value_counts())
print("\nDistribuição de classes (representatividade):")
print(train_df_sem_dup['rotulo'].value_counts(normalize=True))

print("\n----------------------------------")

print("\nDistribuição de classes (valor absoluto):")
print(test_df_sem_dup['rotulo'].value_counts())
print("\nDistribuição de classes (representatividade):")
print(test_df_sem_dup['rotulo'].value_counts(normalize=True))


Distribuição de classes (valor absoluto):
rotulo
NEGATIVE    23505
POSITIVE    17701
Name: count, dtype: int64

Distribuição de classes (representatividade):
rotulo
NEGATIVE    0.570427
POSITIVE    0.429573
Name: proportion, dtype: float64

----------------------------------

Distribuição de classes (valor absoluto):
rotulo
NEGATIVE    5851
POSITIVE    4552
Name: count, dtype: int64

Distribuição de classes (representatividade):
rotulo
NEGATIVE    0.562434
POSITIVE    0.437566
Name: proportion, dtype: float64


Mesmo depois de tirar a duplicidade as observações dos dois rótulo ficam equilibradas.

Iremos agora separa os nossos conjuntos em X e y

In [ ]:
## Dados com Stemização

X_train_ste = train_df['sequencias_padded_ste']
y_train_ste = train_df['rotulo']

X_test_ste = test_df['sequencias_padded_ste']
y_test_ste = test_df['rotulo']

## Dados com Lematização

X_train_lem = train_df['sequencias_padded_lem']
y_train_lem = train_df['rotulo']

X_test_lem = test_df['sequencias_padded_lem']
y_test_lem = test_df['rotulo']

## Dados com Stemização e sem duplicidade

X_train_sem_dup_ste = train_df_sem_dup['sequencias_padded_ste']
y_train_sem_dup_ste = train_df_sem_dup['rotulo']

X_test_sem_dup_ste = test_df_sem_dup['sequencias_padded_ste']
y_test_sem_dup_ste = test_df_sem_dup['rotulo']

## Dados com Lematização e sem duplicidade

X_train_sem_dup_lem = train_df_sem_dup['sequencias_padded_lem']
y_train_sem_dup_lem = train_df_sem_dup['rotulo']

X_test_sem_dup_lem = test_df_sem_dup['sequencias_padded_lem']
y_test_sem_dup_lem = test_df_sem_dup['rotulo']

In [ ]:
# Conversão para NumPy (recomendado para redes neurais)
X_train_ste = np.array(X_train_ste.tolist())
X_test_ste = np.array(X_test_ste.tolist())
y_train_ste = np.array(y_train_ste.tolist())
y_test_ste = np.array(y_test_ste.tolist())


X_train_lem = np.array(X_train_lem.tolist())
X_test_lem = np.array(X_test_lem.tolist())
y_train_lem = np.array(y_train_lem.tolist())
y_test_lem = np.array(y_test_lem.tolist())

In [ ]:
print('---------- X_train_lem ----------')
print(X_train_lem)
print('---------- y_train_lem ----------')
print(y_train_lem)

---------- X_train_lem ----------
['[462, 3799, 3936, 2283, 2917, 2063, 549, 2204, 3822, 2009, 3965, 3804, 3527, 3966, 1985, 2882, 2139, 2950, 2739, 4156, 3034, 1370, 4100, 2503, 1619, 608, 3920, 2296, 1230, 3384, 2663, 2063, 549, 1785, 0, 0, 0, 0, 0, 0]'
 '[4119, 324, 2542, 2468, 2176, 2783, 592, 2729, 2951, 2077, 2862, 1247, 2427, 917, 1485, 2439, 2372, 700, 3693, 3058, 3785, 3540, 3822, 3108, 3023, 3186, 2805, 2931, 209, 4034, 2542, 1306, 1382, 4096, 0, 0, 0, 0, 0, 0]'
 '[753, 3097, 3764, 2221, 3146, 3146, 4085, 1338, 1972, 383, 747, 3187, 462, 3529, 194, 2461, 3918, 2624, 4220, 1224, 3112, 2352, 700, 2869, 4157, 84, 3491, 2915, 4119, 3525, 1224, 3058, 1332, 3966, 2404, 3525, 3119, 1875, 0, 0]'
 ...
 '[3529, 2932, 3146, 3216, 3046, 277, 1264, 64, 1231, 1874, 3040, 4021, 3507, 3377, 2404, 4183, 277, 3301, 1302, 3529, 3040, 2283, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]'
 '[3247, 1279, 3529, 311, 3416, 2829, 84, 4085, 394, 3846, 3507, 309, 2420, 1242, 2468, 2144, 2209, 94

Faremos o mesmo processo para o conjunto sem duplicidade:

In [ ]:
# Conversão para NumPy (recomendado para redes neurais)
X_train_sem_dup_ste = np.array(X_train_sem_dup_ste.tolist())
X_test_sem_dup_ste = np.array(X_test_sem_dup_ste.tolist())
y_train_sem_dup_ste = np.array(y_train_sem_dup_ste.tolist())
y_test_sem_dup_ste = np.array(y_test_sem_dup_ste.tolist())


X_train_sem_dup_lem = np.array(X_train_sem_dup_lem.tolist())
X_test_sem_dup_lem = np.array(X_test_sem_dup_lem.tolist())
y_train_sem_dup_lem = np.array(y_train_sem_dup_lem.tolist())
y_test_sem_dup_lem = np.array(y_test_sem_dup_lem.tolist())

In [ ]:
print('---------- X_test_sem_dup_lem ----------')
print(X_test_sem_dup_lem)
print('---------- y_test_sem_dup_lem ----------')
print(y_test_sem_dup_lem)

---------- X_test_sem_dup_lem ----------
['[2542, 4047, 1972, 1701, 2634, 4034, 1972, 4034, 3350, 2869, 4198, 1438, 1338, 3452, 2824, 4034, 4092, 1338, 1505, 4198, 3373, 2913, 1776, 3486, 4034, 1098, 2829, 2207, 1660, 984, 1485, 1306, 814, 2315, 0, 0, 0, 0, 0, 0]'
 '[3296, 2225, 448, 4220, 3687, 1849, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]'
 '[565, 2283, 2183, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]'
 ...
 '[194, 2634, 1944, 928, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]'
 '[3551, 0, 3843, 1637, 2176, 93, 3864, 1106, 104, 1701, 1302, 3296, 4106, 2710, 2874, 2024, 2160, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]'
 '[1775, 1451, 529, 2326, 3911, 3529, 2283, 1774, 964, 1273, 3416, 3813, 0, 996, 1284, 2522, 106, 3229, 0, 901, 3129, 2874, 2950, 277, 2890, 1284, 1302, 0

#8 Construção do Modelo de Redes Neurais

Primeiro vale a pena explicar um pouco sobre as Redes Neurais.

As Redes Neurais são modelos computacionais inspirados no cérebro humano. Elas são compostas por camadas de neurônios artificiais que processam informações, aprendendo padrões nos dados por meio de conexões ajustáveis chamadas pesos. As redes podem ser usadas para resolver problemas complexos, como reconhecimento de imagens, processamento de linguagem natural (NLP) e previsão de séries temporais.

No nosso caso iremos utilizar o LSTM (Long Short-Term Memory), que é um tipo de rede neural recorrente (RNN) especialmente projetado para trabalhar com dados sequenciais, como textos.

Quais as vantagens do LSTM?

*   Memória de longo prazo: Captura dependências entre palavras distantes na sequência, algo comum em frases.
*   Mitiga o vanishing gradient: Consegue aprender padrões em sequências longas, diferentemente das RNNs tradicionais.
*   Contexto e ordem: Em análises de sentimento, o significado de uma frase depende da ordem das palavras, e o LSTM lida bem com isso.

O LSTM é uma escolha natural para classificar avaliações textuais, já que ele pode capturar nuances e padrões sequenciais que determinam se a avaliação é positiva ou negativa.

**Antes de treinar o modelo precisamos fazer um último tratamento nos dados.**

Neste momento do código, o conjunto X, por mais que seja aparentemente composto por números, ele está em formato de string. Para passar os dados de treino e teste pela rede neural é necessário transformá-los em dados numéricos.

O conjunto y também precisa ser numérico para que a rede neural consega calcular a função de custo.  

Além desse tratamento, iremos adicionar uma dimensão extra nos vetores X's para ter compatibilidade com o modelo LSTM.

Basicamente, o LSTM espera entradas com pelo menos 3 dimensões: número de amostras, comprimento da sequência e número de características por passo de tempo (1, neste caso, porque cada token tem apenas um valor). Esse formato é obrigatório para que a LSTM possa interpretar corretamente os dados como sequências temporais.

In [ ]:
# Conversão de X_train_ste para array numérico
X_train_ste = np.array([np.fromstring(seq.strip('[]'), sep=',') for seq in X_train_ste], dtype=np.float32)

# Adicionando uma dimensão extra para compatibilidade com o modelo LSTM
X_train_ste = np.expand_dims(X_train_ste, axis=-1)  # Agora tem forma (n_samples, 100, 1)

# Conversão de y_train_ste para valores binários
y_train_ste = np.array([1 if label == 'POSITIVE' else 0 for label in y_train_ste], dtype=np.float32)

# Para validação também
X_test_ste = np.array([np.fromstring(seq.strip('[]'), sep=',') for seq in X_test_ste], dtype=np.float32)
X_test_ste = np.expand_dims(X_test_ste, axis=-1)

y_test_ste = np.array([1 if label == 'POSITIVE' else 0 for label in y_test_ste], dtype=np.float32)

In [ ]:
print('---------- y_test_ste ----------')
print(y_test_ste)
print('---------- X_test_ste ----------')
print(X_test_ste)

---------- y_test_ste ----------
[1. 1. 1. ... 0. 0. 0.]
---------- X_test_ste ----------
[[[1893.]
  [2758.]
  [1454.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[2463.]
  [ 863.]
  [ 340.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[ 421.]
  [1685.]
  [1613.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 ...

 [[ 147.]
  [1959.]
  [1431.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[1396.]
  [   0.]
  [2985.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[1313.]
  [1058.]
  [ 394.]
  ...
  [   0.]
  [   0.]
  [   0.]]]


In [ ]:
# Conversão de X_train_lem para array numérico
X_train_lem = np.array([np.fromstring(seq.strip('[]'), sep=',') for seq in X_train_lem], dtype=np.float32)

# Adicionando uma dimensão extra para compatibilidade com o modelo LSTM
X_train_lem = np.expand_dims(X_train_lem, axis=-1)  # Agora tem forma (n_samples, 100, 1)

# Conversão de y_train_lem para valores binários
y_train_lem = np.array([1 if label == 'POSITIVE' else 0 for label in y_train_lem], dtype=np.float32)

# Para validação também
X_test_lem = np.array([np.fromstring(seq.strip('[]'), sep=',') for seq in X_test_lem], dtype=np.float32)
X_test_lem = np.expand_dims(X_test_lem, axis=-1)

y_test_lem = np.array([1 if label == 'POSITIVE' else 0 for label in y_test_lem], dtype=np.float32)

In [ ]:
print('---------- y_test_lem ----------')
print(y_test_lem)
print('---------- X_test_lem ----------')
print(X_test_lem)

---------- y_test_lem ----------
[1. 1. 1. ... 0. 0. 0.]
---------- X_test_lem ----------
[[[2542.]
  [4047.]
  [1972.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[3296.]
  [2225.]
  [ 448.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[ 565.]
  [2283.]
  [2183.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 ...

 [[ 194.]
  [2634.]
  [1944.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[3551.]
  [   0.]
  [3843.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[1775.]
  [1451.]
  [ 529.]
  ...
  [   0.]
  [   0.]
  [   0.]]]


In [ ]:
# Conversão de X_train_sem_dup_ste para array numérico
X_train_sem_dup_ste = np.array([np.fromstring(seq.strip('[]'), sep=',') for seq in X_train_sem_dup_ste], dtype=np.float32)

# Adicionando uma dimensão extra para compatibilidade com o modelo LSTM
X_train_sem_dup_ste = np.expand_dims(X_train_sem_dup_ste, axis=-1)  # Agora tem forma (n_samples, 100, 1)

# Conversão de y_train_sem_dup_ste para valores binários
y_train_sem_dup_ste = np.array([1 if label == 'POSITIVE' else 0 for label in y_train_sem_dup_ste], dtype=np.float32)

# Para validação também
X_test_sem_dup_ste = np.array([np.fromstring(seq.strip('[]'), sep=',') for seq in X_test_sem_dup_ste], dtype=np.float32)
X_test_sem_dup_ste = np.expand_dims(X_test_sem_dup_ste, axis=-1)

y_test_sem_dup_ste = np.array([1 if label == 'POSITIVE' else 0 for label in y_test_sem_dup_ste], dtype=np.float32)

In [ ]:
print('---------- y_test_sem_dup_ste ----------')
print(y_test_sem_dup_ste)
print('---------- X_test_sem_dup_ste ----------')
print(X_test_sem_dup_ste)

---------- y_test_sem_dup_ste ----------
[1. 1. 1. ... 0. 0. 0.]
---------- X_test_sem_dup_ste ----------
[[[1893.]
  [2758.]
  [1454.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[2463.]
  [ 863.]
  [ 340.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[ 421.]
  [1685.]
  [1613.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 ...

 [[ 147.]
  [1959.]
  [1431.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[1396.]
  [   0.]
  [2985.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[1313.]
  [1058.]
  [ 394.]
  ...
  [   0.]
  [   0.]
  [   0.]]]


In [ ]:
# Conversão de X_train_sem_dup_lem para array numérico
X_train_sem_dup_lem = np.array([np.fromstring(seq.strip('[]'), sep=',') for seq in X_train_sem_dup_lem], dtype=np.float32)

# Adicionando uma dimensão extra para compatibilidade com o modelo LSTM
X_train_sem_dup_lem = np.expand_dims(X_train_sem_dup_lem, axis=-1)  # Agora tem forma (n_samples, 100, 1)

# Conversão de y_train_lem para valores binários
y_train_sem_dup_lem = np.array([1 if label == 'POSITIVE' else 0 for label in y_train_sem_dup_lem], dtype=np.float32)

# Para validação também
X_test_sem_dup_lem = np.array([np.fromstring(seq.strip('[]'), sep=',') for seq in X_test_sem_dup_lem], dtype=np.float32)
X_test_sem_dup_lem = np.expand_dims(X_test_sem_dup_lem, axis=-1)

y_test_sem_dup_lem = np.array([1 if label == 'POSITIVE' else 0 for label in y_test_sem_dup_lem], dtype=np.float32)

In [ ]:
print('---------- y_test_sem_dup_lem ----------')
print(y_test_sem_dup_lem)
print('---------- X_test_sem_dup_lem ----------')
print(X_test_sem_dup_lem)

---------- y_test_sem_dup_lem ----------
[1. 1. 1. ... 0. 0. 0.]
---------- X_test_sem_dup_lem ----------
[[[2542.]
  [4047.]
  [1972.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[3296.]
  [2225.]
  [ 448.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[ 565.]
  [2283.]
  [2183.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 ...

 [[ 194.]
  [2634.]
  [1944.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[3551.]
  [   0.]
  [3843.]
  ...
  [   0.]
  [   0.]
  [   0.]]

 [[1775.]
  [1451.]
  [ 529.]
  ...
  [   0.]
  [   0.]
  [   0.]]]


## 8.1 Defindo o modelo

**Descrevendo o modelo:**

O modelo será criado dentro de um for para que possamos testar os 4 conjuntos de dados que criamos. A versão incial dele será formada pelo seguinte código:

    modelo = Sequential()
    modelo.add(LSTM(128, input_shape=(50, 1), return_sequences=False))
    modelo.add(Dropout(0.5))
    modelo.add(Dense(1, activation='sigmoid'))
    modelo.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])



1.    modelo = Sequential()
      *  Cria um modelo sequencial, que é uma pilha linear de camadas. Vamos utilizar esse modelo poir iremos adicionar as camadas uma após a outra, de forma simples e direta.

2.   modelo.add(LSTM(128, input_shape=(100, 1), return_sequences=False))
      *  Adiciona uma camada LSTM ao modelo.
        *  128: Define o número de unidades (neurônios) da camada LSTM. Este número controla a capacidade do modelo de aprender padrões.
        *  input_shape=(50, 1): Especifica o formato da entrada. Aqui, cada amostra tem uma sequência de 50 passos (tokens) com 1 característica por passo.
        *  return_sequences=False: Faz com que a LSTM retorne apenas o estado final da sequência, em vez de uma saída para cada passo. Isso reduz a dimensionalidade e é útil em tarefas como classificação, onde apenas uma decisão final é necessária.

3.   modelo.add(Dropout(0.5))
      *  Adiciona uma camada de Dropout para regularizar o modelo e reduzir o risco de overfitting.
        *  0.5: Indica que 50% dos neurônios na camada anterior serão desativados aleatoriamente durante o treinamento. Isso força o modelo a ser mais robusto, evitando que ele dependa excessivamente de combinações específicas de neurônios.

4.   modelo.add(Dense(1, activation='sigmoid'))
      *  Adiciona uma camada densa (totalmente conectada) que gera a saída do modelo.
        *  1: Define que haverá apenas um neurônio de saída, pois este é um problema de classificação binária (positivo ou negativo).
        *  activation='sigmoid': Aplica a função de ativação sigmoide, que comprime o valor de saída entre 0 e 1. Isso transforma a saída em uma probabilidade, ideal para classificação binária.

5.   modelo.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
      *  Configura o modelo para o treinamento.
        *  optimizer='adam': Escolhe o otimizador Adam, que combina as vantagens de dois outros otimizadores populares (AdaGrad e RMSProp) e ajusta automaticamente os passos de aprendizagem.
        *  loss='binary_crossentropy': Define a função de perda como a entropia cruzada binária, adequada para problemas de classificação binária. Essa função mede a diferença entre as probabilidades previstas pelo modelo e os rótulos reais.
        *  metrics=['accuracy']: Especifica que a métrica de desempenho a ser monitorada durante o treinamento será a acurácia, que mede a proporção de previsões corretas.

## 8.2 Treinando o modelo

Vamos criar uma função para treinar e avaliar o modelo. Depois passar os conjuntos de dados pela função

**IMPORTANTE: O CÓDIGO ABAIXO DEMOROU CERCA DE 30 MINUTOS PARA RODAR**

In [ ]:


# Função para treinar, avaliar e medir o tempo do modelo
def treinar_e_avaliar(modelo, X_train, y_train, X_test, y_test, conjunto_nome):
    print(f"\nTreinando modelo com o {conjunto_nome}...")
    inicio = time.time()  # Marca o tempo inicial

    # Treinamento do modelo
    history = modelo.fit(X_train, y_train, epochs=5, batch_size=64, verbose=0)

    # Avaliação do modelo
    resultados = modelo.evaluate(X_test, y_test, verbose=0)

    fim = time.time()  # Marca o tempo final
    duracao = fim - inicio  # Calcula a duração
    print(f"{conjunto_nome}: Loss = {resultados[0]:.4f}, Acurácia = {resultados[1]:.4f}, Tempo = {duracao:.2f} segundos")
    print(resultados)

    return resultados[1], duracao  # Retorna a acurácia e o tempo

# Lista dos conjuntos de dados
conjuntos = [
    ("Tratamento 1", X_train_ste, y_train_ste, X_test_ste, y_test_ste),
    ("Tratamento 2", X_train_lem, y_train_lem, X_test_lem, y_test_lem),
    ("Tratamento 3", X_train_sem_dup_ste, y_train_sem_dup_ste, X_test_sem_dup_ste, y_test_sem_dup_ste),
    ("Tratamento 4", X_train_sem_dup_lem, y_train_sem_dup_lem, X_test_sem_dup_lem, y_test_sem_dup_lem),
]

# Comparação dos conjuntos
resultados = {}
for nome, X_train, y_train, X_test, y_test in conjuntos:
    # Cria o modelo novamente para cada conjunto
    modelo = Sequential()
    modelo.add(LSTM(128, input_shape=(40, 1), return_sequences=False))
    modelo.add(Dropout(0.5))
    modelo.add(Dense(1, activation='sigmoid'))
    modelo.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

    # Treina, avalia e mede o tempo
    acuracia, duracao = treinar_e_avaliar(modelo, X_train, y_train, X_test, y_test, nome)
    resultados[nome] = {'Acurácia': acuracia, 'Tempo': duracao }



Treinando modelo com o Tratamento 1...
Tratamento 1: Loss = 0.5902, Acurácia = 0.6893, Tempo = 356.23 segundos
[0.5901527404785156, 0.6893148422241211]

Treinando modelo com o Tratamento 2...
Tratamento 2: Loss = 0.5912, Acurácia = 0.6890, Tempo = 351.38 segundos
[0.591247022151947, 0.6890301704406738]

Treinando modelo com o Tratamento 3...
Tratamento 3: Loss = 0.5953, Acurácia = 0.6851, Tempo = 384.75 segundos
[0.5952509641647339, 0.6850908398628235]

Treinando modelo com o Tratamento 4...
Tratamento 4: Loss = 0.5968, Acurácia = 0.6855, Tempo = 308.39 segundos
[0.5968297123908997, 0.6854753494262695]


## 8.3 Avaliando o modelo

Mostrando os resultados de cada treinamento e escolhendo o melhor com base na acurácia do modelo.

**IMPORTANTE: O CÓDIGO ABAIXO SÓ IRÁ FUNCIONAR SE RODAMOS O CÓDIGO ANTERIOR**

Aqui estamos apenas mostrando o resultado final de uma forma mais organizada.

In [ ]:
# Exibe os resultados finais
print("\nResumo dos Resultados:")
for nome, stats in resultados.items():
    print(f"{nome}: Acurácia = {stats['Acurácia']:.4f}, Tempo = {stats['Tempo']:.2f} segundos")

# Melhor conjunto com base na acurácia
melhor_conjunto = max(resultados, key=lambda x: resultados[x]['Acurácia'])
print(f"\nO melhor conjunto é {melhor_conjunto} com Acurácia = {resultados[melhor_conjunto]['Acurácia']:.4f} e duração de treinamento de {resultados[melhor_conjunto]['Tempo']:.0f} ")


Resumo dos Resultados:
Tratamento 1: Acurácia = 0.6893, Tempo = 356.23 segundos
Tratamento 2: Acurácia = 0.6890, Tempo = 351.38 segundos
Tratamento 3: Acurácia = 0.6851, Tempo = 384.75 segundos
Tratamento 4: Acurácia = 0.6855, Tempo = 308.39 segundos

O melhor conjunto é Tratamento 1 com Acurácia = 0.6893 e duração de treinamento de 356 


Perceba que os conjuntos sem duplicidade (treinamento 3 e 4) não truxeram um ganho significativo em acurácia e nem em duração no treinamento do modelo. Também não identificamos diferenças significativas quando comparamos os conjuntos com o tratamento de Lematização (treinamento 2 e 4) com os com  tratamento de Stemização. Por mais que o conjunto com maior acurácia foi o com o tratamento de Stemização e sem retirada de duplicidade, a diferença da acurácia para o conjunto com Lematização e sem duplicidade foi de 0,003. No geral, os resultados dos quatro treinamentos são extremamentes parecidos.

Rodamos os código acima diversas vezes, tivemos casos onde o conjunto 2 obteve a maior acurácia e casos em que o conjunto com o melhor desempenho foi o com o tratamento 1 ou 4. Porém, sempre gerando em torno de 69% de acurácia.

Decimos então ficar com os conjuntos do treinamento 2 e 4. Vamos testar variar alguns parâmetros do modelo com esses dois conjuntos para escolher ficar apenas com o melhor modelo.

## 8.4 Otimizando o modelo

Agora que já escolhemos o conjunto de dados vamos então otimizar o nosso modelo.

### Teste 1

Dados com o Tratamento 2:

**IMPORTANTE: NÃO RODAR DE NOVO A CÉLULA ABAIXO, POIS DEMOROU ALGUMAS HORAS PARA RODAR**

In [ ]:
# Função para construir o modelo
def criar_modelo(units=128, dropout_rate=0.5):
    modelo = Sequential()
    modelo.add(LSTM(units, input_shape=(50, 1), return_sequences=False))
    modelo.add(Dropout(dropout_rate))
    modelo.add(Dense(1, activation='sigmoid'))
    modelo.compile(optimizer=Adam(), loss='binary_crossentropy', metrics=['accuracy'])
    return modelo

# Criação do wrapper para uso com GridSearchCV
modelo = KerasClassifier(model=criar_modelo, verbose=0)

# Definição dos hiperparâmetros
parametros = {
    'model__units': [64, 128],        # Testa diferentes tamanhos de camada LSTM
    'model__dropout_rate': [0.3, 0.5],  # Testa diferentes taxas de Dropout
    'batch_size': [32, 64],          # Tamanhos de batch
    'epochs': [5, 10],                # Diferentes números de épocas
}

# Calcula o tempo de treinamento
inicio = time.time()  # Marca o tempo inicial

# Realização da busca em grade
grid = GridSearchCV(estimator=modelo, param_grid=parametros, cv=3, verbose=1)
grid_result = grid.fit(X_train_lem, y_train_lem)

fim = time.time()  # Marca o tempo final
duracao = fim - inicio  # Calcula a duração

# Exibição do tempo gasto
print(f"Tempo total para a busca em grade: {duracao:.2f} segundos")

# Exibição dos melhores parâmetros
print("Melhores Parâmetros:")
print(grid_result.best_params_)

# Exibição do tempo gasto
print(f"Tempo total para a busca em grade: {duracao:.2f} segundos")

# Avaliação com o conjunto de teste
melhor_modelo = grid_result.best_estimator_
acuracia_teste = melhor_modelo.score(X_test_lem, y_test_lem)
print(f"Acurácia no conjunto de teste: {acuracia_teste:.4f}")


Fitting 3 folds for each of 16 candidates, totalling 48 fits


/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a l

Tempo total para a busca em grade: 14167.27 segundos
Melhores Parâmetros:
{'batch_size': 64, 'epochs': 10, 'model__dropout_rate': 0.5, 'model__units': 64}
Tempo total para a busca em grade: 14167.27 segundos
Acurácia no conjunto de teste: 0.6982


Relembrando:

O modelo que rodamos a primeira vez usava 128 unidades na camada LSTM, com uma taxa de dropout de 0,5, um batch de 64 e epochs igual a 5. O resultado dele foi de uma acurácia de 0,6890 (considerando o tratamento 2).

Após a rodagem do teste 1 obtivemos que o modelo com a melhor acurácia possui alguns parâmetros diferentes do primeiro modelo, em vez de 128 unidades temos 64 unidade, no lugar de epochs igual a 5 temos epochs igual a 10, o batch e a taxa de dropout permaneceram as mesmas. Por mais que seja uma rede diferente a acurácia desse modelo ficou parecido com o do primeiro modelo, sendo de 0,6982.


Perceba que o processo inteiro que percorreu todas as combinações de parâmetros demorou 14.167,27 segundos, o que dá 236,12 minutos = 3,9 horas. Inicialmente tinhamos escrito 3 possibilidades de cada parâmetro porém ficou muito demorado e seguimos com a apenas 2 possibilidades para cada.

Uma acurácia de quase 70% ainda não agrada, queriamos obter algo maior que 80%. Vamos tentar novamente rodas modelos variando os parâmetros com novas combinações.

**IMPORTANTE: NÃO RODAR DE NOVO ESSE CÓDIGO ABAIXO, POIS DEMOROU ALGUMAS HORAS**

In [ ]:
# Função para construir o modelo
def criar_modelo(units=128, dropout_rate=0.5):
    modelo = Sequential()
    modelo.add(LSTM(units, input_shape=(50, 1), return_sequences=False))
    modelo.add(Dropout(dropout_rate))
    modelo.add(Dense(1, activation='sigmoid'))
    modelo.compile(optimizer=Adam(), loss='binary_crossentropy', metrics=['accuracy'])
    return modelo

# Criação do wrapper para uso com GridSearchCV
modelo = KerasClassifier(model=criar_modelo, verbose=0)

# Definição dos hiperparâmetros
parametros = {
    'model__units': [64],        # Testa diferentes tamanhos de camada LSTM
    'model__dropout_rate': [0.5, 0.7],  # Testa diferentes taxas de Dropout
    'batch_size': [64, 128],          # Tamanhos de batch
    'epochs': [5, 15],                # Diferentes números de épocas
}

# Calcula o tempo de treinamento
inicio = time.time()  # Marca o tempo inicial

# Realização da busca em grade
grid = GridSearchCV(estimator=modelo, param_grid=parametros, cv=3, verbose=1)
grid_result = grid.fit(X_train_lem, y_train_lem)

fim = time.time()  # Marca o tempo final
duracao = fim - inicio  # Calcula a duração

# Exibição do tempo gasto
print(f"Tempo total para a busca em grade: {duracao:.2f} segundos")

# Exibição dos melhores parâmetros
print("Melhores Parâmetros:")
print(grid_result.best_params_)

# Avaliação com o conjunto de teste
melhor_modelo = grid_result.best_estimator_
acuracia_teste = melhor_modelo.score(X_test_lem, y_test_lem)
print(f"Acurácia no conjunto de teste: {acuracia_teste:.4f}")

Fitting 3 folds for each of 8 candidates, totalling 24 fits


/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a l

Tempo total para a busca em grade: 5080.55 segundos
Melhores Parâmetros:
{'batch_size': 64, 'epochs': 15, 'model__dropout_rate': 0.5, 'model__units': 64}
Acurácia no conjunto de teste: 0.6980



O melhor modelo dessas combinações de parâmetros ainda possue uma acurácia menor que 70%. A única variação dos parêmtros escolhido da primeira vez (que usamos o GridSearchCV) foi que o epochs foi igual a 15 enquanto que da outra foi igual a 10.

Perceba que o processo inteiro que percorreu todas as combinações de parâmetros demorou menos tempo, mas também tivemos menos combinações dessa vez. Durou 5.080,55 segundos, o que dá 84,7 minutos = 1.4 hora.



---





### Teste 2

Dados com o Tratamento 4:

**IMPORTANTE: NÃO RODAR DE NOVO ESSE CÓDIGO ABAIXO, POIS DEMOROU ALGUMAS HORAS**

In [ ]:
# Função para construir o modelo
def criar_modelo(units=128, dropout_rate=0.5):
    modelo = Sequential()
    modelo.add(LSTM(units, input_shape=(50, 1), return_sequences=False))
    modelo.add(Dropout(dropout_rate))
    modelo.add(Dense(1, activation='sigmoid'))
    modelo.compile(optimizer=Adam(), loss='binary_crossentropy', metrics=['accuracy'])
    return modelo

# Criação do wrapper para uso com GridSearchCV
modelo = KerasClassifier(model=criar_modelo, verbose=0)

# Definição dos hiperparâmetros
parametros = {
    'model__units': [64, 128],        # Testa diferentes tamanhos de camada LSTM
    'model__dropout_rate': [0.3, 0.5],  # Testa diferentes taxas de Dropout
    'batch_size': [32, 64],          # Tamanhos de batch
    'epochs': [5, 10],                # Diferentes números de épocas
}

# Calcula o tempo de treinamento
inicio = time.time()  # Marca o tempo inicial

# Realização da busca em grade
grid = GridSearchCV(estimator=modelo, param_grid=parametros, cv=3, verbose=1)
grid_result = grid.fit(X_train_sem_dup_lem, y_train_sem_dup_lem)

fim = time.time()  # Marca o tempo final
duracao = fim - inicio  # Calcula a duração

# Exibição do tempo gasto
print(f"Tempo total para a busca em grade: {duracao:.2f} segundos")

# Exibição dos melhores parâmetros
print("Melhores Parâmetros:")
print(grid_result.best_params_)

# Exibição do tempo gasto
print(f"Tempo total para a busca em grade: {duracao:.2f} segundos")

# Avaliação com o conjunto de teste
melhor_modelo = grid_result.best_estimator_
acuracia_teste = melhor_modelo.score(X_test_sem_dup_lem, y_test_sem_dup_lem)
print(f"Acurácia no conjunto de teste: {acuracia_teste:.4f}")


Fitting 3 folds for each of 16 candidates, totalling 48 fits


/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a l

Tempo total para a busca em grade: 15532.80 segundos
Melhores Parâmetros:
{'batch_size': 64, 'epochs': 10, 'model__dropout_rate': 0.5, 'model__units': 128}
Tempo total para a busca em grade: 15532.80 segundos
Acurácia no conjunto de teste: 0.6937


Aqui o modelo que foi escolhido como o melhor (com base na acurácia) do teste da célula anterior foi o com o batch size de 64, epochs de 10, dropout de 0.5 e 128 unidade. Porém perceba que a sua acurácia foi de 0,6937, ou seja, foi uma acurácia quase nada menor que as dos últimos modelos destacados como os melhores nas células anteriores, como o conjunto com o tratamento 2.

Perceba que o processo inteiro que percorreu todas as combinações de parâmetros demorou 15.532,8 segundos, o que dá 259 minutos = 4,3 horas.

Testando outros parâmetros:

**IMPORTANTE: NÃO RODAR DE NOVO ESSE CÓDIGO ABAIXO, POIS DEMOROU ALGUMAS HORAS**

In [ ]:
# Função para construir o modelo
def criar_modelo(units=128, dropout_rate=0.5):
    modelo = Sequential()
    modelo.add(LSTM(units, input_shape=(50, 1), return_sequences=False))
    modelo.add(Dropout(dropout_rate))
    modelo.add(Dense(1, activation='sigmoid'))
    modelo.compile(optimizer=Adam(), loss='binary_crossentropy', metrics=['accuracy'])
    return modelo

# Criação do wrapper para uso com GridSearchCV
modelo = KerasClassifier(model=criar_modelo, verbose=0)

# Definição dos hiperparâmetros
parametros = {
    'model__units': [64],        # Testa diferentes tamanhos de camada LSTM
    'model__dropout_rate': [0.5, 0.7],  # Testa diferentes taxas de Dropout
    'batch_size': [64, 128],          # Tamanhos de batch
    'epochs': [5, 15],                # Diferentes números de épocas
}

# Calcula o tempo de treinamento
inicio = time.time()  # Marca o tempo inicial

# Realização da busca em grade
grid = GridSearchCV(estimator=modelo, param_grid=parametros, cv=3, verbose=1)
grid_result = grid.fit(X_train_sem_dup_lem, y_train_sem_dup_lem)

fim = time.time()  # Marca o tempo final
duracao = fim - inicio  # Calcula a duração

# Exibição do tempo gasto
print(f"Tempo total para a busca em grade: {duracao:.2f} segundos")

# Exibição dos melhores parâmetros
print("Melhores Parâmetros:")
print(grid_result.best_params_)

# Avaliação com o conjunto de teste
melhor_modelo = grid_result.best_estimator_
acuracia_teste = melhor_modelo.score(X_test_sem_dup_lem, y_test_sem_dup_lem)
print(f"Acurácia no conjunto de teste: {acuracia_teste:.4f}")

Fitting 3 folds for each of 8 candidates, totalling 24 fits


/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)
/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a l

Tempo total para a busca em grade: 5229.09 segundos
Melhores Parâmetros:
{'batch_size': 64, 'epochs': 15, 'model__dropout_rate': 0.7, 'model__units': 64}
Acurácia no conjunto de teste: 0.6968


De novo não conseguimos chegar em uma rede com acurácia melhor que 70%.

O processo inteiro da célula anterior demorou 5.229,09 segundos, o que dá 87 minutos = 1.45 hora.

### Teste 3

Vamos agora testar outras variações do modelo.
Vamos tentar:

*   Adicionar mais uma camadas, como a Dense, para tentar capturar representações mais complexas
*   Adicionar camadas de normalização para estabilizar o aprendizado e melhorar a convergência
*   Utilizar outros otimizadores, como *RMSprop* e *SGD*
*   Utilizar outra função de ativação, como a *tanh*
*   Utilizar *recurrent_dropout* na camada LSTM para regularizar as conexões recorrentes
*   Aplicar um Early Stopping para evita overfitting e reduzir o tempo de treinamento interrompendo-o quando o desempenho de validação não melhorar

**IMPORTANTE: NÃO RODAR DE NOVO ESSE CÓDIGO ABAIXO, POIS DEMOROU ALGUMAS HORAS**

In [ ]:

#from tensorflow.keras.layers import BatchNormalization
#from tensorflow.keras.callbacks import EarlyStopping
#from tensorflow.keras.optimizers import  RMSprop, SGD
#from sklearn.metrics import accuracy_score

# Função para criar o modelo base
def criar_modelo(base_model=False, aumento_camadas=False, batch_norm=False,
                 otimizador='adam', ativacao='sigmoid', regularizacao=False, early_stopping=False):
    modelo = Sequential()

    # Camada LSTM principal
    modelo.add(LSTM(128, input_shape=(40, 1), return_sequences=False,
                    dropout=0.5 if regularizacao else 0.0,
                    recurrent_dropout=0.2 if regularizacao else 0.0))

    # Aumento de Camadas
    if aumento_camadas:
        modelo.add(Dense(64, activation='relu'))
        modelo.add(Dropout(0.3))

    # Batch Normalization
    if batch_norm:
        modelo.add(BatchNormalization())

    # Camada de saída
    modelo.add(Dense(1, activation=ativacao))

    # Compilação
    opt = {'adam': Adam(), 'rmsprop': RMSprop(), 'sgd': SGD(learning_rate=0.01)}[otimizador]
    modelo.compile(optimizer=opt, loss='binary_crossentropy', metrics=['accuracy'])

    return modelo

# Função para treinar e avaliar o modelo
def treinar_e_avaliar(modelo, X_train, y_train, X_test, y_test, early_stopping=False):
    callbacks = []
    if early_stopping:
        callbacks.append(EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True))

    inicio = time.time()
    history = modelo.fit(X_train, y_train,
                         validation_split=0.2,
                         epochs=10,
                         batch_size=64,
                         verbose=0,
                         callbacks=callbacks)
    fim = time.time()
    duracao = fim - inicio

    # Avaliação no conjunto de teste
    y_pred = (modelo.predict(X_test) > 0.5).astype(int)
    acuracia = accuracy_score(y_test, y_pred)

    return acuracia, duracao

# Dados
X_train = X_train_lem
y_train = y_train_lem
X_test = X_test_lem
y_test = y_test_lem

# Configurações para testar
testes = [
    {'descricao': 'Modelo Base', 'args': {}},
    {'descricao': 'Aumento de Camadas', 'args': {'aumento_camadas': True}},
    {'descricao': 'Batch Normalization', 'args': {'batch_norm': True}},
    {'descricao': 'Otimizador RMSprop', 'args': {'otimizador': 'rmsprop'}},
    {'descricao': 'Otimizador SGD', 'args': {'otimizador': 'sgd'}},
    {'descricao': 'Ativação tanh', 'args': {'ativacao': 'tanh'}},
    {'descricao': 'Regularização', 'args': {'regularizacao': True}},
    {'descricao': 'Early Stopping', 'args': {'early_stopping': True}},
]

# Executando os testes
resultados = []
for teste in testes:
    print(f"\nTestando: {teste['descricao']}")
    modelo = criar_modelo(**teste['args'])
    acuracia, duracao = treinar_e_avaliar(modelo, X_train, y_train, X_test, y_test,
                                          early_stopping=teste['args'].get('early_stopping', False))
    resultados.append({'Descrição': teste['descricao'], 'Acurácia': acuracia, 'Tempo': duracao})
    print(f"Acurácia: {acuracia:.4f}, Tempo: {duracao:.2f} segundos")

# Exibindo os resultados
print("\nResultados Finais:")
for res in resultados:
    print(f"{res['Descrição']}: Acurácia = {res['Acurácia']:.4f}, Tempo = {res['Tempo']:.2f} segundos")



Testando: Modelo Base
330/330 ━━━━━━━━━━━━━━━━━━━━ 7s 21ms/step
Acurácia: 0.6889, Tempo: 809.19 segundos

Testando: Aumento de Camadas


/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


330/330 ━━━━━━━━━━━━━━━━━━━━ 7s 21ms/step
Acurácia: 0.6889, Tempo: 742.00 segundos

Testando: Batch Normalization


/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


330/330 ━━━━━━━━━━━━━━━━━━━━ 9s 28ms/step
Acurácia: 0.6853, Tempo: 660.89 segundos

Testando: Otimizador RMSprop


...

330/330 ━━━━━━━━━━━━━━━━━━━━ 7s 20ms/step
Acurácia: 0.6883, Tempo: 686.66 segundos

Testando: Regularização


/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


330/330 ━━━━━━━━━━━━━━━━━━━━ 9s 26ms/step
Acurácia: 0.6837, Tempo: 743.39 segundos

Testando: Early Stopping


/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


330/330 ━━━━━━━━━━━━━━━━━━━━ 8s 23ms/step
Acurácia: 0.6902, Tempo: 661.65 segundos

Resultados Finais:
Modelo Base: Acurácia = 0.6889, Tempo = 809.19 segundos
Aumento de Camadas: Acurácia = 0.6889, Tempo = 742.00 segundos
Batch Normalization: Acurácia = 0.6853, Tempo = 660.89 segundos
Otimizador RMSprop: Acurácia = 0.6836, Tempo = 703.36 segundos
Otimizador SGD: Acurácia = 0.6882, Tempo = 633.82 segundos
Ativação tanh: Acurácia = 0.6883, Tempo = 686.66 segundos
Regularização: Acurácia = 0.6837, Tempo = 743.39 segundos
Early Stopping: Acurácia = 0.6902, Tempo = 661.65 segundos


Conseguimos chegar numa acurácia de 69% com o Early Stopping, porém sua acurácia é praticamente igual a que encontramos no primeiro teste dessa seção 8.

O processo inteiro da célula anterior demorou 5.640,96 segundos, o que dá 94 minutos = 1.56 hora.

### Teste 4

Vamos testar passar os nossos dados por um modelo pré-treinado como o BERT. Para isso vamos utilizar o pipeline da Hugging Face, que simplifica o uso de modelos pré-treinados para tarefa desse projeto. Para utlizar o pipeline precisamos voltar com o campo da avaliação para o formato texto.

In [ ]:
# Revertendo tokens para texto
def tokens_para_texto(tokens, index_to_word):
    # Convert tokens to a list of integers to ensure hashability
    tokens = tokens.astype(int).flatten().tolist()
    return ' '.join(index_to_word.get(token, '') for token in tokens)

# Reverter os conjuntos de treino e teste
X_train_lem_novo = [tokens_para_texto(seq, index_to_word_lem) for seq in X_train_lem]
X_test_lem_novo = [tokens_para_texto(seq, index_to_word_lem) for seq in X_test_lem]



In [ ]:
print(X_train_lem_novo)

['started logging restart phone whereas never used minor annoyance try log back tell go online complete tap connect met black screen nothing else happens really see way around uninstall reinstall fix never used problem      ', 'play many great album different type reggae rock soul oldie rap heavy metal hiphop new artist pick choose free ad premium deal annoyance interruption cost monthly basis also ðÿžµ lyric great feature sing along      ', 'always preferred streaming service year year ago would use pandora iheart liked started using like changed life maybe let people without subscription choose least one day though actually play want people ad usually go youtube want something special  ', 'recently got premium everytime skip next crash                                 ', '                                       ', 'like ad                                      ', 'great annoying ad easy use perfect                                  ', 'find want work offline anywhere great job           

In [ ]:
print(X_test_lem_novo)

['great easy use thing wish lyric use lyric past least little bit would nice full lyric available would pay little extra option saying ðÿ lyric appreciate update look forward seeing new feature add future      ', 'good mobile replay let u recommend                                  ', 'even phone window                                     ', 'new update buggy keep disappearing open keep going also freeze open liked download track restart really like little                      ', 'ðÿ  better sound quality minimum ad good âºï                               ', ' work team keep                                    ', 'work well easy navigate                                    ', 'change lock screen saver stupid ever install screen saver lock one know remove apart fantastic iam going uninstall remove screen saver                   ', 'changed way session worked longer single phone also changed way join session slight inconvenience beta testing since recent update much worse rest great coming y

In [ ]:
#from transformers import BertTokenizer, TFBertForSequenceClassification

In [ ]:
# Criar o pipeline
classifier = pipeline('text-classification', model='bert-base-uncased')

# Aplicar no conjunto de teste (X_test_lem_novo)
y_pred = [1 if result['label'] == 'POSITIVE' else 0 for result in classifier(X_test_lem_novo)]

# Avaliar acurácia
acuracia = accuracy_score(y_test, y_pred)  # y_test é a lista de rótulos reais (0 ou 1)
print(f"Acurácia no conjunto de teste: {acuracia:.4f}")

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Acurácia no conjunto de teste: 0.5565


Pereceba que a acurácia desse modelo deu muito abaixo dos modelos anteriores que testamos no teste 1, 2 e 3.

### Teste 5

Vamos aumentar os epochs para ver se melhora o resultado da rede neural.
Considerando 50 epochs.

**IMPORTANTE: NÃO RODAR DE NOVO A CÉLULA ABAIXO, POIS DEMOROU ALGUMAS HORAS PARA RODAR**

In [ ]:
# Testando um modelo com 50 epochs
teste5_model = Sequential()
teste5_model.add(LSTM(64, input_shape=(40, 1), return_sequences=False))
teste5_model.add(Dropout(0.5))
teste5_model.add(Dense(1, activation='sigmoid'))
teste5_model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])


# Treinar o modelo
inicio = time.time()  #
teste5_model.fit(X_train_lem, y_train_lem, epochs=50, batch_size=64, verbose=1)
fim = time.time()  # Marca o tempo final
duracao = fim - inicio  # Calcula a duração

/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Epoch 1/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 23s 27ms/step - accuracy: 0.6629 - loss: 0.6122
Epoch 2/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 18s 27ms/step - accuracy: 0.6978 - loss: 0.5857
Epoch 3/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 28s 43ms/step - accuracy: 0.6921 - loss: 0.5897
Epoch 4/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 32s 49ms/step - accuracy: 0.6940 - loss: 0.5871
Epoch 5/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 29s 44ms/step - accuracy: 0.6956 - loss: 0.5842
Epoch 6/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 29s 27ms/step - accuracy: 0.6946 - loss: 0.5850
Epoch 7/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 21s 27ms/step - accuracy: 0.6968 - loss: 0.5858
Epoch 8/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 20s 27ms/step - accuracy: 0.6961 - loss: 0.5851
Epoch 9/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 21s 31ms/step - accuracy: 0.6948 - loss: 0.5872
Epoch 10/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 33s 51ms/step - accuracy: 0.6969 - loss: 0.5853
Epoch 11/50
659/659 ━━━━━━━━━━━━━━━━━━━━ 36s 43ms/step - accuracy: 0.6936 - loss: 0.5875
Epoch 12/50
659/659 ━━━━━━━━━━

Testando com o conjunto de teste o modelo gerado.

In [ ]:
# Fazer predições com o modelo carregado
y_pred_proba = teste5_model.predict(X_test_lem)
y_pred = (y_pred_proba > 0.5).astype(int).flatten()  # Converte probabilidades para rótulos binários

# Avaliar resultados
acuracia = accuracy_score(y_test_lem, y_pred)
print(f"Acurácia: {acuracia:.4f}")
print("\nRelatório de classificação:")
print(classification_report(y_test_lem, y_pred, target_names=['negative', 'positive']))

330/330 ━━━━━━━━━━━━━━━━━━━━ 3s 8ms/step
Acurácia: 0.6879

Relatório de classificação:
              precision    recall  f1-score   support

    negative       0.69      0.79      0.74      5864
    positive       0.68      0.56      0.61      4674

    accuracy                           0.69     10538
   macro avg       0.69      0.67      0.68     10538
weighted avg       0.69      0.69      0.68     10538



### Teste 6

Vamos aumentar os epochs para ver se melhora o resultado da rede neural.
Considerando 200 epochs.

**IMPORTANTE: NÃO RODAR DE NOVO A CÉLULA ABAIXO, POIS DEMOROU 7 HORAS PARA RODAR**

In [ ]:
# Testando um modelo com 200 epochs
teste6_model = Sequential()
teste6_model.add(LSTM(256, input_shape=(40, 1), return_sequences=False))
teste6_model.add(Dropout(0.5))
teste6_model.add(Dense(1, activation='sigmoid'))
teste6_model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])


# Treinar o modelo
inicio = time.time()  #
teste6_model.fit(X_train_lem, y_train_lem, epochs=200, batch_size=64, verbose=1)
fim = time.time()  # Marca o tempo final
duracao = fim - inicio  # Calcula a duração

/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Epoch 1/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 143s 201ms/step - accuracy: 0.6708 - loss: 0.6084
Epoch 2/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 121s 170ms/step - accuracy: 0.6931 - loss: 0.5887
Epoch 3/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 140s 167ms/step - accuracy: 0.6939 - loss: 0.5869
Epoch 4/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 141s 167ms/step - accuracy: 0.6995 - loss: 0.5828
Epoch 5/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 142s 166ms/step - accuracy: 0.6936 - loss: 0.5867
Epoch 6/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 141s 165ms/step - accuracy: 0.6921 - loss: 0.5867
Epoch 7/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 108s 164ms/step - accuracy: 0.6981 - loss: 0.5844
Epoch 8/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 141s 163ms/step - accuracy: 0.6931 - loss: 0.5869
Epoch 9/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 144s 166ms/step - accuracy: 0.6951 - loss: 0.5840
Epoch 10/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 143s 168ms/step - accuracy: 0.6917 - loss: 0.5873
Epoch 11/200
659/659 ━━━━━━━━━━━━━━━━━━━━ 107s 163ms/step - accuracy: 0.6969 - loss: 0.58

Testando com o conjunto de teste o modelo gerado.

In [ ]:
# Fazer predições com o modelo carregado
y_pred_proba = teste6_model.predict(X_test_lem)
y_pred = (y_pred_proba > 0.5).astype(int).flatten()  # Converte probabilidades para rótulos binários

# Avaliar resultados
acuracia = accuracy_score(y_test_lem, y_pred)
print(f"Acurácia: {acuracia:.4f}")
print("\nRelatório de classificação:")
print(classification_report(y_test_lem, y_pred, target_names=['negative', 'positive']))

330/330 ━━━━━━━━━━━━━━━━━━━━ 13s 38ms/step
Acurácia: 0.6846

Relatório de classificação:
              precision    recall  f1-score   support

    negative       0.71      0.74      0.72      5864
    positive       0.65      0.62      0.63      4674

    accuracy                           0.68     10538
   macro avg       0.68      0.68      0.68     10538
weighted avg       0.68      0.68      0.68     10538



## 8.5 Escolhendo o modelo final

Iremos seguir com o modelo identificado como o melhor na etápa 8.4, Teste 5. O modelo que obteve a acurácia no conjunto de teste de 0.69 tem os seguintes parâmetros:

    'batch_size': 64
    'epochs': 50,
    'model__dropout_rate': 0.5,
    'model__units': 64

**Treinando modelo final**

Vamos então agora re-treinar a nossa rede neural com todos os dados que temos (treino e teste combinados), pois isso aumenta o volume de dados usado para ajuste dos pesos e pode melhorar a performance da rede.

**IMPORTANTE: NÃO RODAR DE NOVO A CÉLULA ABAIXO, POIS DEMOROU 30 MINUTOS PARA RODAR**

In [ ]:
# Combinar dados de treino e teste
X_total = np.concatenate((X_train_lem, X_test_lem), axis=0)
y_total = np.concatenate((y_train_lem, y_test_lem), axis=0)

# Definir o modelo final com os melhores parâmetros
final_model = Sequential()
final_model.add(LSTM(64, input_shape=(40, 1), return_sequences=False))
final_model.add(Dropout(0.5))
final_model.add(Dense(1, activation='sigmoid'))
final_model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])


# Treinar o modelo com todos os dados
final_model.fit(X_total, y_total, epochs=50, batch_size=64, verbose=1)

Epoch 1/50


/usr/local/lib/python3.10/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


824/824 ━━━━━━━━━━━━━━━━━━━━ 23s 25ms/step - accuracy: 0.6765 - loss: 0.6029
Epoch 2/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 22s 27ms/step - accuracy: 0.6915 - loss: 0.5914
Epoch 3/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 41s 27ms/step - accuracy: 0.6933 - loss: 0.5875
Epoch 4/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 41s 27ms/step - accuracy: 0.6909 - loss: 0.5883
Epoch 5/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 21s 25ms/step - accuracy: 0.6902 - loss: 0.5901
Epoch 6/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 43s 28ms/step - accuracy: 0.6933 - loss: 0.5848
Epoch 7/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 40s 27ms/step - accuracy: 0.6969 - loss: 0.5838
Epoch 8/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 41s 27ms/step - accuracy: 0.6983 - loss: 0.5834
Epoch 9/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 41s 27ms/step - accuracy: 0.6962 - loss: 0.5858
Epoch 10/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 21s 25ms/step - accuracy: 0.6945 - loss: 0.5859
Epoch 11/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 41s 26ms/step - accuracy: 0.6953 - loss: 0.5852
Epoch 12/50
824/824 ━━━━━━━━━━━━━━━━━━━━ 

**Exportando o modelo final**

In [ ]:
# Salvar o modelo em formato .h5
final_model.save("final_model.h5")

**Importando o modelo final**

In [ ]:
import requests
from tensorflow.keras.models import load_model

# URL do arquivo .h5 no GitHub (link bruto)
url = "https://raw.githubusercontent.com/fernanda-valente-postgraduate/pos-graduacao-ciencia-de-dados/main/projeto-sprint-3/final_model.h5"

# Baixar o arquivo
response = requests.get(url)
with open("final_model.h5", "wb") as f:
    f.write(response.content)

# Carregar o modelo
# Vou deixar como final_model_2 só para ter um nome diferente, porém ele é igual ao final_model
final_model_2 = load_model("final_model.h5")

# Testar o modelo
print("Modelo carregado com sucesso:", final_model_2)

Modelo carregado com sucesso: <Sequential name=sequential_2, built=True>


# 9 Validando modelo com novos dados

Vamos então testar o nosso modelo com novos dados.

As avaliações abaixo não são reais.

In [ ]:
# Dados fictícios: avaliações e classificações
data = {
    "review": [
        "This app is amazing! I can listen to my favorite music anytime.",
        "Not good for users, especially if you try to use offline, it dosen't work at all",
        "Great playlists and recommendations. Love it!",
        "Spotify changed to much, it doesn't give time to process the changes and then more thing arrives. I don't like it",
        "The sound quality is excellent. Highly recommended.",
        "First, I couldn't find some song from my favorite artist, then when I found the quality of the audio wasn't good",
        "It's user-friendly and has a vast music library.",
        "I can't download songs anymore",
        "Family plan is great value for money",
        "Too high of a price, I'm not going to spend money on an app that doesn't give the best",
        "Love the offline mode",
        "Too many bugs, every time I open the app a new bug appears, it's so annoying i gave up",
        "The shuffle feature is broken. Songs repeat constantly.",
        "Podcasts are great, and I use them daily.",
        "It's better than other music apps I've tried.",
        "I lost all my playlists after an update. Awful experience.",
        "The UI is clean and intuitive. Easy to navigate.",
        "Doesn't support many languages. Needs improvement.",
        "Excellent for discovering new artists.",
        "The app is full of bugs and needs has to many ads.",
        "Audio ads are way too frequent for free users.",
        "Love the personalized recommendations.",
        "Crashes every day, there is not one single day a try to open the Spotify app that I don't get frustrated",
        "Works well on my phone but not on my tablet.",
        "The lyrics feature is a great addition.",
        "Why do ads play after every other song? It feels like punishment for using free.",
        "Spotify Wrapped is my favorite part of the year.",
        "Too many issues with playback.",
        "It's a lifesaver during long commutes.",
        "Not happy with the recent updates. Feels clunky.",
        "I lost all my playlists, they had more then 100 songs in it. I'm not going to spend more time in this app",
        "My favorite artists are all here. Super convenient!",
        "Playback stops randomly. Can't enjoy the experience.",
        "The curated playlists are on point.",
        "Constant crashes after the latest update.",
        "Super fast streaming. Rarely buffers.",
        "Free plan isn't worth it. Too many restrictions.",
        "The integration with smart devices is seamless.",
        "The ads are misleading and annoying.",
        "Finally, an app that understands music lovers!",
        "I can't sync between my phone and laptop. Frustrating.",
        "The equalizer feature is great for audiophiles.",
        "It's so difficult to enjoy the music with so many ads",
        "I love how I can follow my favorite artists.",
        "Even with premium trials, they sneak in ads, which feels dishonest and unfair.",
        "Great for discovering niche genres.",
        "Why do I keep getting irrelevant recommendations?",
        "The sleep timer is a brilliant feature.",
        "Some songs disappear from my playlist. Not okay!",
        "The dark mode is soothing and stylish.",
        "Too many ads ruin the experience, especially for free users. It’s unbearable!",
        "Perfect companion for workouts. Motivating playlists!",
        "Six consecutive ads before a song? That’s just disrespectful to users' time.",
        "Amazing sound quality even on free plan.",
        "The recent update removed key features, and the interface is now very confusing.",
        "Love the integration with gaming consoles.",
        "Downloads keep failing. Waste of time.",
        "The artist radio feature is a game-changer.",
        "Frequent glitches during playback ruin the mood.",
        "Great deals for students. Affordable and reliable.",
        "Customer support is useless, and there’s no way to get help when things go wrong",
        "The app design is modern and appealing.",
        "The subscription cancellation process is a nightmare.",
        "I enjoy how it adapts to my music taste.",
        "Not enough options for customizing playlists.",
        "Reliable during road trips. Always works offline.",
        "The ad volume is much louder than the music.",
        "The podcasts selection is outstanding.",
        "Ads are way too frequent and often louder than the music, which is very annoying.",
        "It's like having a DJ on my phone.",
        "The recommendation algorithm feels outdated.",
        "I can finally organize my library easily.",
        "The free trial auto-renewed without my consent.",
        "It syncs well with my car's audio system.",
        "Some features are hard to find in the menu.",
        "The app is constantly improving. I love it!",
        "The repeat button isn't working properly.",
        "Great for language learning through songs.",
        "Why is the app so slow after the update?",
        "Helps me focus during work. Great playlists.",
        "I keep losing downloaded songs. So frustrating!",
        "I appreciate the curated playlists for every mood.",
        "The app often forgets where I stopped a song.",
        "I love how it connects me with global music trends.",
        "The app's performance is inconsistent across devices.",
        "Love how it brings back nostalgic tracks.",
        "It's not worth the subscription price anymore.",
        "The download speed is impressive. Works instantly.",
        "Sometimes, the app won't open. Annoying bug.",
        "I love the real-time lyrics display. Great feature!",
        "Playback speed control is a fantastic addition.",
        "It feels like the app keeps getting worse over time.",
        "I finally found a platform with all my favorite genres.",
        "The customer support chatbot is useless.",
        "The sound normalization is perfect for my playlists.",
        "I don't like how it's hard to share playlists.",
        "The algorithm is spot-on with my music taste.",
        "I wish it supported higher-quality audio streaming.",
        "The student discount plan makes it affordable for me.",
        "I often experience lag when using Bluetooth.",
    ],
    "label": ["POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "NEGATIVE",
              "POSITIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",
              "POSITIVE",
              "NEGATIVE",]
              }

# Criar DataFrame
df_new_reviews = pd.DataFrame(data)

# Mostrar as primeiras linhas do dataframe
print(df_new_reviews.head())



                                              review     label
0  This app is amazing! I can listen to my favori...  POSITIVE
1  Not good for users, especially if you try to u...  NEGATIVE
2      Great playlists and recommendations. Love it!  POSITIVE
3  Spotify changed to much, it doesn't give time ...  NEGATIVE
4  The sound quality is excellent. Highly recomme...  POSITIVE


Precisamos tratar esses dados antes de passar pelo modelo

In [ ]:
!pip install contractions

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 289.9/289.9 kB 6.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.7/110.7 kB 4.8 MB/s eta 0:00:00


In [ ]:
import nltk
import re
import string
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
import contractions


# Baixar pacotes necessários
nltk.download('stopwords')
nltk.download('punkt_tab')
nltk.download('wordnet')
nltk.download('omw-1.4')


# Configurações
stop_words = set(stopwords.words('english'))
lemmatizer = WordNetLemmatizer()
comprimento_maximo = 40

# Adicionar palavras adicionais irrelevantes ao conjunto de stopwords
additional_stopwords = {'app', 'music', 'play', 'spotify', 'song', 'songs', 'listen', 'playing', 'get', 'playlist'}
stop_words.update(additional_stopwords)

# Remover "not" do conjunto padrão de stopwords
stop_words = stop_words - {'not'}

# Adicionar palavras irrelevantes ao conjunto ajustado
stop_words.update(additional_stopwords)

# Funções

def expandir_contracoes(texto):
    return contractions.fix(texto)

def filtrar_stopwords(texto):
    # Dividir o texto em palavras
    palavras = word_tokenize(texto)
    # Remover stopwords e pontuações
    palavras_filtradas = [palavra for palavra in palavras if palavra.lower() not in stop_words  and palavra not in string.punctuation]
    return " ".join(palavras_filtradas)

# Criar o dicionário `word_to_index_lem` a partir de `index_to_word_lem`
word_to_index_lem = {word: idx for idx, word in index_to_word_lem.items()}

def tokens_para_indices(tokens, word_to_index):
    return [word_to_index.get(token, 0) for token in tokens]  # 0 para palavras fora do vocabulário

def aplicar_lematizacao(tokens):
    return [lemmatizer.lemmatize(palavra) for palavra in tokens]

def normalizar_texto(texto):
    texto = texto.lower()  # Converter para minúsculas
    texto = re.sub(r'[^\w\s]', '', texto)  # Remover pontuação
    texto = re.sub(r'\d+', '', texto)  # Remover números
    texto = re.sub(r'\s+', ' ', texto).strip()  # Remover múltiplos espaços e espaços extras
    return texto


# Aplicar pré-processamento
df_new_reviews['avaliacao_tratada'] = df_new_reviews['review'].apply(expandir_contracoes)
df_new_reviews['avaliacao_tratada'] = df_new_reviews['avaliacao_tratada'].dropna().apply(filtrar_stopwords)
df_new_reviews['avaliacao_tratada'] = df_new_reviews['avaliacao_tratada'].apply(normalizar_texto)


# Tokenização e lematização
df_new_reviews['tokens'] = df_new_reviews['avaliacao_tratada'].apply(word_tokenize)
df_new_reviews['tokens_lemmatizados'] = df_new_reviews['tokens'].apply(aplicar_lematizacao)

# Converter tokens para índices usando o vocabulário existente
df_new_reviews['sequencias'] = df_new_reviews['tokens_lemmatizados'].apply(lambda x: tokens_para_indices(x, word_to_index_lem))

# Aplicar padding
df_new_reviews['sequencias_padded'] = pad_sequences(df_new_reviews['sequencias'], maxlen=comprimento_maximo, padding='post').tolist()


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


Vendo como ficaram os dados tratados:

In [ ]:
print(df_new_reviews.head(5))

                                              review     label
0  This app is amazing! I can listen to my favori...  POSITIVE
1  Not good for users, especially if you try to u...  NEGATIVE
2      Great playlists and recommendations. Love it!  POSITIVE
3  Spotify changed to much, it doesn't give time ...  NEGATIVE
4  The sound quality is excellent. Highly recomme...  POSITIVE


In [ ]:
print(df_new_reviews.tail(5))

                                               review     label
95     I don't like how it's hard to share playlists.  NEGATIVE
96      The algorithm is spot-on with my music taste.  POSITIVE
97  I wish it supported higher-quality audio strea...  NEGATIVE
98  The student discount plan makes it affordable ...  POSITIVE
99       I often experience lag when using Bluetooth.  NEGATIVE


Passando pelo modelo final:

In [ ]:
# Converter rótulos para numérico (0 para 'negative', 1 para 'positive')
df_new_reviews['label_numeric'] = df_new_reviews['label'].map({'POSITIVE': 1, 'NEGATIVE': 0})

# Transformar 'sequencias_padded' em array NumPy
X_new = np.array(df_new_reviews['sequencias_padded'].tolist())
y_true = df_new_reviews['label_numeric'].values

# Fazer predições com o modelo carregado
y_pred_proba = final_model_2.predict(X_new)
y_pred = (y_pred_proba > 0.5).astype(int).flatten()  # Converte probabilidades para rótulos binários

# Avaliar resultados
acuracia = accuracy_score(y_true, y_pred)
print(f"Acurácia: {acuracia:.4f}")
print("\nRelatório de classificação:")
print(classification_report(y_true, y_pred, target_names=['NEGATIVE', 'POSITIVE']))

4/4 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step 
Acurácia: 0.6300

Relatório de classificação:
              precision    recall  f1-score   support

    NEGATIVE       0.89      0.31      0.46        51
    POSITIVE       0.57      0.96      0.72        49

    accuracy                           0.63       100
   macro avg       0.73      0.64      0.59       100
weighted avg       0.73      0.63      0.59       100



O modelo apresentou uma acurácia de 63%, indicando um desempenho moderado, mas ainda com espaço para melhorias significativas. O relatório de classificação revela os seguintes pontos:

* **Classe negativa**: A precisão foi alta (0.89), o que significa que, das avaliações identificadas como negativas, a maioria era realmente negativa. No entanto, o recall foi baixo (0.31), indicando que o modelo deixou de identificar muitas avaliações negativas. O F1-score foi 0.46, refletindo o desequilíbrio entre precisão e recall para essa classe.

* **Classe positiva**: O recall foi excelente (0.96), sugerindo que o modelo conseguiu capturar quase todas as avaliações positivas do conjunto. Entretanto, a precisão foi apenas 0.57, indicando uma proporção significativa de falsas positivas. O F1-score de 0.72 reflete um desempenho mais balanceado, ainda que longe do ideal.

* **Média ponderada e macro**: O F1-score médio ponderado e a macro média foram ambos 0.59, evidenciando que o modelo apresentou dificuldades em equilibrar o desempenho entre as duas classes.

Esses resultados sugerem que o modelo é melhor em identificar avaliações positivas, mas enfrenta desafios significativos na detecção de avaliações negativas, especialmente em termos de recall.

Vamos ver as classificações incorretas:

In [ ]:
# Criar uma coluna com as previsões
df_new_reviews['predicted_label'] = ['POSITIVE' if pred == 1 else 'NEGATIVE' for pred in y_pred]

# Identificar os casos incorretos
df_erros = df_new_reviews[df_new_reviews['label'] != df_new_reviews['predicted_label']]

# Exibir os casos errados
print(f"Número de classificações incorretas: {len(df_erros)}")
df_erros[['review', 'label', 'predicted_label']]


Número de classificações incorretas: 37


review     label  \
7                      I can't download songs anymore  NEGATIVE   
12  The shuffle feature is broken. Songs repeat co...  NEGATIVE   
15  I lost all my playlists after an update. Awful...  NEGATIVE   
19  The app is full of bugs and needs has to many ...  NEGATIVE   
23       Works well on my phone but not on my tablet.  NEGATIVE   
25  Why do ads play after every other song? It fee...  NEGATIVE   
27                     Too many issues with playback.  NEGATIVE   
34          Constant crashes after the latest update.  NEGATIVE   
38               The ads are misleading and annoying.  NEGATIVE   
40  I can't sync between my phone and laptop. Frus...  NEGATIVE   
42  It's so difficult to enjoy the music with so m...  NEGATIVE   
44  Even with premium trials, they sneak in ads, w...  NEGATIVE   
46  Why do I keep getting irrelevant recommendations?  NEGATIVE   
48   Some songs disappear from my playlist. Not okay!  NEGATIVE   
52  Six consecutive ads before a song? That’s just...  NEGATIVE   
56             Downloads keep failing. Waste of time.  NEGATIVE   
58   Frequent glitches during playback ruin the mood.  NEGATIVE   
62  The subscription cancellation process is a nig...  NEGATIVE   
64      Not enough options for customizing playlists.  NEGATIVE   
65  Reliable during road trips. Always works offline.  POSITIVE   
66       The ad volume is much louder than the music.  NEGATIVE   
70       The recommendation algorithm feels outdated.  NEGATIVE   
72    The free trial auto-renewed without my consent.  NEGATIVE   
73          It syncs well with my car's audio system.  POSITIVE   
74        Some features are hard to find in the menu.  NEGATIVE   
76          The repeat button isn't working properly.  NEGATIVE   
78           Why is the app so slow after the update?  NEGATIVE   
80    I keep losing downloaded songs. So frustrating!  NEGATIVE   
82      The app often forgets where I stopped a song.  NEGATIVE   
84  The app's performance is inconsistent across d...  NEGATIVE   
86     It's not worth the subscription price anymore.  NEGATIVE   
88       Sometimes, the app won't open. Annoying bug.  NEGATIVE   
91  It feels like the app keeps getting worse over...  NEGATIVE   
93           The customer support chatbot is useless.  NEGATIVE   
95     I don't like how it's hard to share playlists.  NEGATIVE   
97  I wish it supported higher-quality audio strea...  NEGATIVE   
99       I often experience lag when using Bluetooth.  NEGATIVE   

   predicted_label  
7         POSITIVE  
12        POSITIVE  
15        POSITIVE  
19        POSITIVE  
23        POSITIVE  
25        POSITIVE  
27        POSITIVE  
34        POSITIVE  
38        POSITIVE  
40        POSITIVE  
42        POSITIVE  
44        POSITIVE  
46        POSITIVE  
48        POSITIVE  
52        POSITIVE  
56        POSITIVE  
58        POSITIVE  
62        POSITIVE  
64        POSITIVE  
65        NEGATIVE  
66        POSITIVE  
70        POSITIVE  
72        POSITIVE  
73        NEGATIVE  
74        POSITIVE  
76        POSITIVE  
78        POSITIVE  
80        POSITIVE  
82        POSITIVE  
84        POSITIVE  
86        POSITIVE  
88        POSITIVE  
91        POSITIVE  
93        POSITIVE  
95        POSITIVE  
97        POSITIVE  
99        POSITIVE

Praticamente tudo que foi classificado incorretamente foi uma avaliação negativa, tirando 2 casos de avaliação positiva.

Esse resultado pode indicar que o modelo foi treinado em um conjunto de dados desbalanceado e por isso acaba tentendo para classificação positiva. Vamos verificar se a variável targets estava desbalanceada mesmo:

In [ ]:
print("Distribuição do conjunto de TREINO:")
print('Quantidade de avaliações positivas: ',y_train_lem.sum())
print('Quantidade de avaliações: ',len(y_train_lem))
print('Representatividade: ', y_train_lem.sum()/len(y_train_lem))


Distribuição do conjunto de TREINO:
Quantidade de avaliações positivas:  18589.0
Quantidade de avaliações:  42148
Representatividade:  0.4410410932903103


In [ ]:
print("Distribuição do conjunto de TESTE:")
print('Quantidade de avaliações positivas: ',y_test_lem.sum())
print('Quantidade de avaliações: ',len(y_test_lem))
print('Representatividade: ', y_test_lem.sum()/len(y_test_lem))


Distribuição do conjunto de TESTE:
Quantidade de avaliações positivas:  4674.0
Quantidade de avaliações:  10538
Representatividade:  0.44353767318276716


Não estavam.

Vamos testar passar o modelo pelo conjunto de teste para ver o resultado.




In [ ]:
# Fazer predições com o modelo carregado
y_pred_proba = final_model_2.predict(X_test_lem)
y_pred = (y_pred_proba > 0.5).astype(int).flatten()  # Converte probabilidades para rótulos binários

# Avaliar resultados
acuracia = accuracy_score(y_test_lem, y_pred)
print(f"Acurácia: {acuracia:.4f}")
print("\nRelatório de classificação:")
print(classification_report(y_test_lem, y_pred, target_names=['negative', 'positive']))

330/330 ━━━━━━━━━━━━━━━━━━━━ 3s 10ms/step
Acurácia: 0.6865

Relatório de classificação:
              precision    recall  f1-score   support

    negative       0.68      0.82      0.74      5864
    positive       0.70      0.52      0.60      4674

    accuracy                           0.69     10538
   macro avg       0.69      0.67      0.67     10538
weighted avg       0.69      0.69      0.68     10538



O resultado ficou parecido com o que esperávemos com uma acurácia de 69%.

# 10 Conclusão

Neste projeto, demonstramos a importância da análise de dados para extrair informações valiosas de um conjunto de dados reais. Por meio de transformações e análises, ilustramos como cálculos simples, como média, mediana, contagem de caractéres e palavras, quartis e percentis, como esses cálulos combinados com visualizações gráficas, podem oferecer insights significativos. O tratamento adequado dos dados textuais foi essencial para garantir a qualidade do treinamento do modelo.

O foco foi desenvolver uma rede neural capaz de classificar avaliações de usuários do Spotify como positivas ou negativas. Realizamos uma limpeza e pré-processamento robustos das avaliações, incluindo tokenização, remoção de stopwords e padronização do texto. Em seguida, treinamos o modelo com sequências numéricas representando as palavras, utilizando técnicas modernas de processamento de linguagem natural (NLP).

Testamos diversas posibilidades para os hiperparâmetros e chegamos em um modelo com uma acurácia de 69%. A precisão do modelo ao identificar o sentimento das avaliações deixou um pouco a desejar. Os resultados da seção 9 sugerem que o modelo final é melhor em identificar avaliações positivas, mas enfrenta desafios significativos na detecção de avaliações negativas. Acredito que esse projeto pode ter uma segunda versão com os seguintes passos:


*   Treinar o modelo com novos dados que serão disponibilizados conforme o uso do aplicativo por novos usuários, focando em pegar uma variabilidade maior de avaliações diferentes e focando em entender melhor as avaliações negativas.
*   Testar modelos clássicos de problema de classificação
*   Testar redes neurais mais robustas


O aprendizado extraído desse projeto reforça que os números e textos, por si só, não têm valor; é o tratamento e a análise cuidadosa que possibilitam transformar dados em conhecimento acionável. É extremante importante ter senso crítico para avaliar e refazer os modelos, identificando pontos de melhoria e falhas. Que possamos continuar utilizando dados para inovar e tomar decisões mais inteligentes no futuro!